In [ ]:
"""
LangGraph Tutorial: State Initialization Patterns - Unit 2.3 Exercise 7
==================================================

> **Joint Initiative:** This tutorial is part of a collaboration between [AI Product Engineer](https://aiproduct.engineer) and the [Nebius Academy](https://academy.nebius.com).

This tutorial demonstrates how to implement robust state initialization for
multi-tool agents in LangGraph. You'll learn how to create flexible, type-safe
state containers and manage tool configurations effectively.

Key Concepts Covered:
1. State Structure Design
2. Tool Configuration Management
3. Dynamic Tool Setup
4. Type-Safe Initialization
5. Configuration Flexibility
"""

In [ ]:
import uuid
from typing import Annotated, Any, TypedDict
!pip install langchain-core
!pip install langgraph
from langchain_core.messages import BaseMessage, HumanMessage, SystemMessage
from langgraph.graph.message import add_messages

In [ ]:
"""
Step 1: State Definition
------------------------------
Define the core state structure for multi-tool agents.

Why This Matters:
---------------
State structure is fundamental because:
1. Ensures data consistency
2. Enables type checking
3. Facilitates tool management
4. Supports system scaling

Debug Tips:
----------
1. State Structure:
   - Verify type annotations
   - Check field initialization
   - Monitor state growth
2. Common Issues:
   - Missing required fields
   - Type mismatches
   - Memory leaks
"""

In [ ]:
class State(TypedDict):
    """State container for multi-tool agent.

    Attributes:
        messages: Conversation history
        pending_tools: Tools waiting for execution
        results: Tool execution results
        errors: Error messages
        tool_configs: Tool-specific configurations
    """

    messages: Annotated[list[BaseMessage], add_messages]
    pending_tools: list[dict[str, Any]]
    results: dict[str, Any]
    errors: dict[str, str]
    tool_configs: dict[str, dict[str, Any]]

In [ ]:
"""
Step 2: Tool Call Creation
------------------------------
Implement standardized tool call configuration.

Why This Matters:
---------------
Tool call standardization is crucial because:
1. Ensures consistent tool interface
2. Enables tool tracking
3. Facilitates debugging
4. Supports tool orchestration

Debug Tips:
----------
1. Tool Call Creation:
   - Verify ID generation
   - Check argument formatting
   - Monitor tool name consistency
2. Common Problems:
   - Duplicate tool IDs
   - Malformed arguments
   - Invalid tool names
"""

In [ ]:
def create_tool_call(
    tool_name: str, query: str, tool_id: str | None = None
) -> dict[str, Any]:
    """Create a standardized tool call configuration.

    Args:
        tool_name: Name of the tool to call
        query: Query string for the tool
        tool_id: Optional custom tool ID

    Returns:
        Dictionary containing tool call configuration

    Examples:
        >>> create_tool_call("calculator", "2 + 2")
        {'id': 'calculator_12345678', 'tool_name': 'calculator', 'args': {'query': '2 + 2'}}
    """
    return {
        "id": tool_id or f"{tool_name}_{str(uuid.uuid4())[:8]}",
        "tool_name": tool_name,
        "args": {"query": query},
    }

In [ ]:
"""
Step 3: State Initialization Implementation
------------------------------
Implement flexible state initialization with configuration support.

Why This Matters:
---------------
State initialization is essential because:
1. Sets up initial system state
2. Configures tool behavior
3. Enables customization
4. Establishes baseline state

Debug Tips:
----------
1. Initialization Logic:
   - Verify config merging
   - Check default values
   - Monitor tool setup
2. Common Issues:
   - Missing configurations
   - Invalid tool types
   - Configuration conflicts
"""

In [ ]:
def get_initial_state(
    tool_type: str = "default", config: dict[str, Any] | None = None
) -> State:
    """Initialize state with tool configuration.

    Args:
        tool_type: Type of tools to initialize ("default", "search", "math")
        config: Optional custom configuration

    Returns:
        Initialized State object
    """
    # Define tool configurations
    tool_configs = {
        "calculator": {"name": "calculator", "max_retries": 2, "timeout": 5.0},
        "weather": {"name": "weather", "max_retries": 1, "timeout": 3.0},
        "search": {"name": "search", "max_retries": 1, "timeout": 10.0},
    }

    # Initialize messages
    messages = [
        SystemMessage(content="Initializing multi-tool agent"),
        HumanMessage(content="Ready to process requests"),
    ]

    # Setup tool calls based on type
    if tool_type == "search":
        pending_tools = [
            create_tool_call("search", "capital of France"),
            create_tool_call("search", "largest city in Japan"),
        ]
    elif tool_type == "math":
        pending_tools = [
            create_tool_call("calculator", "2 + 2"),
            create_tool_call("calculator", "sqrt(16)"),
        ]
    else:
        pending_tools = [
            create_tool_call("weather", "London"),
            create_tool_call("calculator", "3 * 4"),
        ]

    # Apply custom config if provided
    if config:
        tool_configs.update(config.get("tool_configs", {}))
        if config.get("pending_tools"):
            pending_tools = config["pending_tools"]

    return {
        "messages": messages,
        "pending_tools": pending_tools,
        "results": {},
        "errors": {},
        "tool_configs": tool_configs,
    }

In [ ]:
"""
Step 4: Demonstration Implementation
------------------------------
Example usage showing initialization patterns.

Why This Matters:
---------------
Demonstration code is valuable because:
1. Shows practical usage patterns
2. Illustrates configuration options
3. Demonstrates customization
4. Provides testing scenarios

Debug Tips:
----------
1. Demo Execution:
   - Monitor initialization
   - Verify configurations
   - Check tool setup
2. Common Problems:
   - Invalid scenarios
   - Configuration errors
   - State corruption
"""

In [ ]:
def demonstrate_initialization():
    """Demonstrate different state initialization scenarios."""
    print("State Initialization Demo")
    print("=" * 50)

    # Test different initialization types
    scenarios = [
        ("Default Setup", "default"),
        ("Search Tools", "search"),
        ("Math Tools", "math"),
        (
            "Custom Config",
            "default",
            {
                "tool_configs": {
                    "custom_tool": {"name": "custom_tool", "timeout": 1.0}
                },
                "pending_tools": [create_tool_call("custom_tool", "test query")],
            },
        ),
    ]

    for scenario in scenarios:
        name, tool_type = scenario[:2]
        config = scenario[2] if len(scenario) > 2 else None

        print(f"\nScenario: {name}")
        state = get_initial_state(tool_type, config)

        print("\nInitial Messages:")
        for msg in state["messages"]:
            print(f"{type(msg).__name__}: {msg.content}")

        print("\nPending Tools:")
        for tool in state["pending_tools"]:
            print(f"- {tool['tool_name']}: {tool['args']['query']}")

        print("\nTool Configurations:")
        for tool, cfg in state["tool_configs"].items():
            print(f"- {tool}: {cfg}")
        print("-" * 50)

In [ ]:
if __name__ == "__main__":
    demonstrate_initialization()

In [ ]:
"""
Common Pitfalls:
1. Configuration Management
   - Missing default values
   - Incorrect merging
   - Lost configurations

2. Tool Setup Issues
   - Invalid tool types
   - Missing tool configs
   - Incorrect initialization

3. State Consistency
   - Incomplete initialization
   - Type mismatches
   - Missing fields

4. Message Management
   - Incorrect message types
   - Missing system messages
   - Inconsistent formatting

Key Takeaways:
1. Flexible Initialization
   - Supports multiple tool types
   - Enables custom configuration
   - Maintains type safety

2. Configuration Patterns
   - Clear default values
   - Proper config merging
   - Tool-specific settings

3. State Management
   - Complete state structure
   - Type-safe operations
   - Clear initialization

Next Steps:
1. Enhanced Configuration
   - Add validation rules
   - Implement schemas
   - Create config presets

2. Tool Management
   - Add dependencies
   - Create tool groups
   - Implement priorities

3. State Validation
   - Add integrity checks
   - Create recovery paths
   - Implement persistence

Expected Output:
State Initialization Demo
==================================================

Scenario: Default Setup

Initial Messages:
SystemMessage: Initializing multi-tool agent
HumanMessage: Ready to process requests

Pending Tools:
- weather: London
- calculator: 3 * 4

Tool Configurations:
- calculator: {'name': 'calculator', 'max_retries': 2, 'timeout': 5.0}
- weather: {'name': 'weather', 'max_retries': 1, 'timeout': 3.0}
- search: {'name': 'search', 'max_retries': 1, 'timeout': 10.0}
--------------------------------------------------

[Additional scenarios output...]
"""